
# 在线学习人脸部件的字典

本示例使用一个大型人脸数据集来学习一组20 x 20的图像块，这些图像块构成人脸。

从编程的角度来看，这很有趣，因为它展示了如何使用scikit-learn的在线API通过分块处理一个非常大的数据集。我们的处理方式是一次加载一张图像，并从这张图像中随机提取50个图像块。当我们积累了500个这样的图像块（使用10张图像）后，我们运行在线KMeans对象MiniBatchKMeans的:func:`~sklearn.cluster.MiniBatchKMeans.partial_fit` 方法。

MiniBatchKMeans的详细设置使我们能够看到在连续调用partial_fit时，一些聚类被重新分配。这是因为它们所代表的图像块数量变得太少，选择一个新的随机聚类会更好。


## 加载数据



In [ ]:
from sklearn import datasets

faces = datasets.fetch_olivetti_faces()

## 学习图像的字典



In [ ]:
import time

import numpy as np

from sklearn.cluster import MiniBatchKMeans
from sklearn.feature_extraction.image import extract_patches_2d

print("Learning the dictionary... ")
rng = np.random.RandomState(0)
kmeans = MiniBatchKMeans(n_clusters=81, random_state=rng, verbose=True, n_init=3)
patch_size = (20, 20)

buffer = []
t0 = time.time()

# 在线学习部分：对整个数据集循环6次
index = 0
for _ in range(6):
    for img in faces.images:
        data = extract_patches_2d(img, patch_size, max_patches=50, random_state=rng)
        data = np.reshape(data, (len(data), -1))
        buffer.append(data)
        index += 1
        if index % 10 == 0:
            data = np.concatenate(buffer, axis=0)
            data -= np.mean(data, axis=0)
            data /= np.std(data, axis=0)
            kmeans.partial_fit(data)
            buffer = []
        if index % 100 == 0:
            print("Partial fit of %4i out of %i" % (index, 6 * len(faces.images)))

dt = time.time() - t0
print("done in %.2fs." % dt)

## 绘制结果



In [ ]:
import matplotlib.pyplot as plt

plt.figure(figsize=(4.2, 4))
for i, patch in enumerate(kmeans.cluster_centers_):
    plt.subplot(9, 9, i + 1)
    plt.imshow(patch.reshape(patch_size), cmap=plt.cm.gray, interpolation="nearest")
    plt.xticks(())
    plt.yticks(())


plt.suptitle(
    "Patches of faces\nTrain time %.1fs on %d patches" % (dt, 8 * len(faces.images)),
    fontsize=16,
)
plt.subplots_adjust(0.08, 0.02, 0.92, 0.85, 0.08, 0.23)

plt.show()